# Lab | Natural Language Processing
### SMS: SPAM or HAM

### Let's prepare the environment

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer

- Read Data for the Fraudulent Email Kaggle Challenge
- Reduce the training set to speead up development. 

In [2]:
## Read Data for the Fraudulent Email Kaggle Challenge
train_data = pd.read_csv(r"C:\Users\jefit\OneDrive\Escritorio\Ironhack\Ironhack candela\Week 4\Labs\lab-natural-language-processing\data\kg_train.csv",encoding='latin-1')

test_data = pd.read_csv(r"C:\Users\jefit\OneDrive\Escritorio\Ironhack\Ironhack candela\Week 4\Labs\lab-natural-language-processing\data\kg_test.csv",encoding='latin-1')
# Reduce the training set to speed up development. 

train_data = train_data.head(1000)
print(train_data.shape)

# Modify for final system

train_data.fillna("",inplace=True)

(1000, 2)


### Let's divide the training and test set into two partitions

In [3]:
# Your code
#from sklearn.model_selection import train_test_split

X = train_data['text']

y = train_data['label']

#X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

## Data Preprocessing

In [4]:
import string
from nltk.corpus import stopwords
print(string.punctuation)
print(stopwords.words("english")[100:110])
from nltk.stem.snowball import SnowballStemmer
snowball = SnowballStemmer('english')

!"#$%&'()*+,-./:;<=>?@[\]^_`{|}~
['needn', "needn't", 'no', 'nor', 'not', 'now', 'o', 'of', 'off', 'on']


## Now, we have to clean the html code removing words

- First we remove inline JavaScript/CSS
- Then we remove html comments. This has to be done before removing regular tags since comments can contain '>' characters
- Next we can remove the remaining tags

In [5]:
import re

def clean_html(X):
    # Remove inline JavaScript/CSS:
    cleaned_no_html = re.sub(r'<(script|style).*?>.*?</\1>', '', X, flags=re.DOTALL)

    # Remove HTML comments:
    cleaned_no_html = re.sub(r'<!--.*?-->', '', cleaned_no_html, flags=re.DOTALL)

    # Remove all remaining HTML tags:
    cleaned_no_html = re.sub(r'<.*?>', '', cleaned_no_html)

    # Remove extra whitespace:
    cleaned_no_html = re.sub(r'\s+', ' ', cleaned_no_html).strip()

    return cleaned_no_html

cleaned_no_html = [clean_html(text) for text in X]

print(cleaned_no_html)

["DEAR SIR, STRICTLY A PRIVATE BUSINESS PROPOSAL I AM MIKE CHUKWU , THE MANAGER, BILLS AND EXCHANGE AT THE FOREIGN REMITTANCE DEPARTMENT OF THE ZENITH INTERNATIONAL BANK PLC. I AM WRITING THIS LETTER TO ASK FOR YOUR SUPPORT AND COOPERATION TO CARRY OUT THIS BUSINESS OPPORTUNITY IN MY DEPARTMENT. WE DISCOVERED AN ABANDONED SUM OF $15,000,000.00 (FIFTEEN MILLION UNITED STATES DOLLARS ONLY) IN AN ACCOUNT THAT BELONGS TO ONE OF OUR FOREIGN CUSTOMERS WHO DIED ALONG WITH HIS ENTIRE FAMILY OF A WIFE AND TWO CHILDREN IN NOVEMBER 1997 IN A PLANE CRASH. SINCE WE HEARD OF HIS DEATH, WE HAVE BEEN EXPECTING HIS NEXT-OF-KIN TO COME OVER AND PUT CLAIMS FOR HIS MONEY AS THE HEIR,BECAUSE WE CANNOT RELEASE THE FUND FROM HIS ACCOUNT UNLESS SOMEONE APPLIES FOR CLAIM AS THE NEXT-OF-KIN TO THE DECEASED AS INDICATED IN OUR BANKING GUIDELINES. UNFORTUNATELY, NEITHER THEIR FAMILY MEMBER NOR DISTANT RELATIVE HAS EVER APPEARED TO CLAIM THE SAID FUND. UPON THIS DISCOVERY,I AND OTHER OFFICIALS IN MY DEPARTMENT HAV

- Remove all the special characters
    
- Remove numbers
    
- Remove all single characters
 
- Remove single characters from the start

- Substitute multiple spaces with single space

- Remove prefixed 'b'

- Convert to Lowercase

In [6]:
def clean_text(cleaned_no_html):
    # Remove special characters (keep only letters and spaces)
    fully_cleaned_text = re.sub(r'[^a-zA-Z\s]', ' ', cleaned_no_html)
    # Remove digits
    fully_cleaned_text = re.sub(r'\d+', '', fully_cleaned_text)
    # Remove all single characters
    fully_cleaned_text = re.sub(r'\s+[a-zA-Z]\s+', ' ', fully_cleaned_text)
    # Remove single characters from the start (e.g., "A quick..." → "quick...")
    fully_cleaned_text = re.sub(r'^[a-zA-Z]\s+', '', fully_cleaned_text)
    # Substitute multiple spaces with a single space
    fully_cleaned_text = re.sub(r'\s+', ' ', fully_cleaned_text)
    # Convert to lowercase
    fully_cleaned_text = fully_cleaned_text.lower().strip()
    return fully_cleaned_text

fully_cleaned_text = [clean_text(text) for text in cleaned_no_html]

fully_cleaned_text

['dear sir strictly private business proposal am mike chukwu the manager bills and exchange at the foreign remittance department of the zenith international bank plc am writing this letter to ask for your support and cooperation to carry out this business opportunity in my department we discovered an abandoned sum of fifteen million united states dollars only in an account that belongs to one of our foreign customers who died along with his entire family of wife and two children in november in plane crash since we heard of his death we have been expecting his next of kin to come over and put claims for his money as the heir because we cannot release the fund from his account unless someone applies for claim as the next of kin to the deceased as indicated in our banking guidelines unfortunately neither their family member nor distant relative has ever appeared to claim the said fund upon this discovery and other officials in my department have agreed to make business with you and releas

## Now let's work on removing stopwords
Remove the stopwords.

In [7]:
# First we need to tokenize the cleaned text:
# For tokenization
from nltk.tokenize import word_tokenize

# For stopword removal
from nltk.corpus import stopwords

tokens = [word_tokenize(word) for word in fully_cleaned_text]

tokens

[['dear',
  'sir',
  'strictly',
  'private',
  'business',
  'proposal',
  'am',
  'mike',
  'chukwu',
  'the',
  'manager',
  'bills',
  'and',
  'exchange',
  'at',
  'the',
  'foreign',
  'remittance',
  'department',
  'of',
  'the',
  'zenith',
  'international',
  'bank',
  'plc',
  'am',
  'writing',
  'this',
  'letter',
  'to',
  'ask',
  'for',
  'your',
  'support',
  'and',
  'cooperation',
  'to',
  'carry',
  'out',
  'this',
  'business',
  'opportunity',
  'in',
  'my',
  'department',
  'we',
  'discovered',
  'an',
  'abandoned',
  'sum',
  'of',
  'fifteen',
  'million',
  'united',
  'states',
  'dollars',
  'only',
  'in',
  'an',
  'account',
  'that',
  'belongs',
  'to',
  'one',
  'of',
  'our',
  'foreign',
  'customers',
  'who',
  'died',
  'along',
  'with',
  'his',
  'entire',
  'family',
  'of',
  'wife',
  'and',
  'two',
  'children',
  'in',
  'november',
  'in',
  'plane',
  'crash',
  'since',
  'we',
  'heard',
  'of',
  'his',
  'death',
  'we',


In [8]:
# Your code

stop_words = set(stopwords.words('english'))

# Remove stopwords from each document
cleaned_text_no_stopwords = [
	[word for word in doc if word not in stop_words]
	for doc in tokens
]

cleaned_text_no_stopwords

train_data['cleaned_text'] = cleaned_text_no_stopwords

train_data['cleaned_text'].head()

0    [dear, sir, strictly, private, business, propo...
1                                                   []
2    [nora, cheryl, emailed, dozens, memos, haiti, ...
3    [dear, sir, fmadam, know, proposal, might, sur...
4                                                [fyi]
Name: cleaned_text, dtype: object

## Tame Your Text with Lemmatization
Break sentences into words, then use lemmatization to reduce them to their base form (e.g., "running" becomes "run"). See how this creates cleaner data for analysis!

In [9]:
# Your code

from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
lemmatized_docs = []
for doc in cleaned_text_no_stopwords:
    lemmatized_doc = [lemmatizer.lemmatize(token) for token in doc]
    lemmatized_docs.append(" ".join(lemmatized_doc))

lemmatized_docs

train_data['lemmatized_words'] = lemmatized_docs

train_data['lemmatized_words'].head()


0    dear sir strictly private business proposal mi...
1                                                     
2    nora cheryl emailed dozen memo haiti weekend p...
3    dear sir fmadam know proposal might surprise e...
4                                                  fyi
Name: lemmatized_words, dtype: object

## Bag Of Words
Let's get the 10 top words in ham and spam messages (**EXPLORATORY DATA ANALYSIS**)

In [10]:
# Your code

from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

vectorizer = CountVectorizer()

X_bow = vectorizer.fit_transform(lemmatized_docs)

print("Bag of Words:\n", X_bow.toarray())
print("Vocabulary:", vectorizer.get_feature_names_out())

Bag of Words:
 [[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
Vocabulary: ['aa' 'aaa' 'aabeiawaeaambiqaceqedeqh' ... 'zzz' 'zzzahbxntxe' 'zzzj']


In [11]:
from collections import Counter
import nltk
nltk.download('punkt')

# Step 1: Separate ham and spam messages
ham_texts = train_data[train_data['label'] == 0]['lemmatized_words']
spam_texts = train_data[train_data['label'] == 1]['lemmatized_words']

# Step 2: Tokenize and flatten into a single list of words
ham_words = [word for text in ham_texts for word in word_tokenize(text)]
spam_words = [word for text in spam_texts for word in word_tokenize(text)]

# Step 3: Count frequencies
ham_freq = Counter(ham_words)
spam_freq = Counter(spam_words)

# Step 4: Show top 10 most common words
print("Top 10 words in HAM messages:")
print(ham_freq.most_common(10))

print("\nTop 10 words in SPAM messages:")
print(spam_freq.most_common(10))

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\jefit\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


Top 10 words in HAM messages:
[('state', 136), ('pm', 127), ('would', 107), ('president', 99), ('time', 95), ('call', 94), ('mr', 91), ('obama', 84), ('percent', 81), ('secretary', 79)]

Top 10 words in SPAM messages:
[('money', 981), ('account', 895), ('bank', 800), ('fund', 781), ('u', 765), ('e', 565), ('transaction', 549), ('business', 514), ('country', 508), ('mr', 489)]


## Extra features

In [12]:
train_data.columns

Index(['text', 'label', 'cleaned_text', 'lemmatized_words'], dtype='object')

In [13]:
# Your code
from sklearn.model_selection import train_test_split

X = train_data.drop('label', axis=1)

y = train_data['label']

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

In [14]:
# We add to the original dataframe two additional indicators (money symbols and suspicious words).
money_simbol_list = "|".join(["euro","dollar","pound","€","$"])
suspicious_words = "|".join(["free","cheap","sex","money","account","bank","fund","transfer","transaction","win","deposit","password"])

X_train['money_mark'] = X_train['cleaned_text'].str.contains(money_simbol_list)*1
X_train['suspicious_words'] = X_train['cleaned_text'].str.contains(suspicious_words)*1
X_train['text_len'] = X_train['cleaned_text'].apply(lambda x: len(x)) 

X_val['money_mark'] = X_val['cleaned_text'].str.contains(money_simbol_list)*1
X_val['suspicious_words'] = X_val['cleaned_text'].str.contains(suspicious_words)*1
X_val['text_len'] = X_val['cleaned_text'].apply(lambda x: len(x)) 

X_train.head()

text  \
29   ----------- REGARDS, MR NELSON SMITH.KINDLY RE...   
535  I have not been able to reach oscar this am. W...   
695  ; Huma Abedin B6I'm checking with Pat on the 5...   
557  I can have it announced here on Monday - can't...   
836      BANK OF AFRICAAGENCE SAN PEDRO14 BP 1210 S...   

                                          cleaned_text  \
29   [regards, mr, nelson, smith, kindly, reply, pr...   
535  [able, reach, oscar, supposed, send, pdb, rece...   
695  [huma, abedin, checking, pat, work, jack, jake...   
557                         [announced, monday, today]   
836  [bank, africaagence, san, pedro, bp, san, pedr...   

                                      lemmatized_words  money_mark  \
29   regard mr nelson smith kindly reply private em...         NaN   
535         able reach oscar supposed send pdb receive         NaN   
695  huma abedin checking pat work jack jake rest a...         NaN   
557                             announced monday today         NaN   
836  bank africaagence san pedro bp san pedro cote ...         NaN   

     suspicious_words  text_len  
29                NaN        12  
535               NaN         7  
695               NaN        14  
557               NaN         3  
836               NaN       159

## How would work the Bag of Words with Count Vectorizer concept?

In [19]:
# Your code

# Use the lemmatized text column for Bag of Words
vectorizer = CountVectorizer()
X_bow = vectorizer.fit_transform(train_data['lemmatized_words'])

print("Bag of Words shape:", X_bow.shape)
print("First 5 feature names:", vectorizer.get_feature_names_out()[:5])
print("First 5 rows of Bag of Words matrix:\n", X_bow[:5].toarray())

Bag of Words shape: (1000, 29929)
First 5 feature names: ['aa' 'aaa' 'aabeiawaeaambiqaceqedeqh' 'aac' 'aaccount']
First 5 rows of Bag of Words matrix:
 [[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


## TD-IDF

- Load the vectorizer

- Vectorize all dataset

- print the shape of the vetorized dataset

In [20]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Load the vectorizer
tfidf_vectorizer = TfidfVectorizer()

# Vectorize the entire dataset using the lemmatized text
X_tfidf = tfidf_vectorizer.fit_transform(train_data['lemmatized_words'])

# Print the shape of the vectorized dataset
print("TF-IDF shape:", X_tfidf.shape)
print("First 5 feature names:", tfidf_vectorizer.get_feature_names_out()[:5])
print("First 5 rows of TF-IDF matrix:\n", X_tfidf[:5].toarray())

TF-IDF shape: (1000, 29929)
First 5 feature names: ['aa' 'aaa' 'aabeiawaeaambiqaceqedeqh' 'aac' 'aaccount']
First 5 rows of TF-IDF matrix:
 [[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


## And the Train a Classifier?

In [21]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, accuracy_score

# Use TF-IDF features for classification
X = X_tfidf
y = train_data['label']

# Split the data (if not already split)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

# Train MultinomialNB classifier
clf = MultinomialNB()
clf.fit(X_train, y_train)

# Predict on validation set
y_pred = clf.predict(X_val)

# Print evaluation metrics
print("Accuracy:", accuracy_score(y_val, y_pred))
print(classification_report(y_val, y_pred))

Accuracy: 0.935
              precision    recall  f1-score   support

           0       1.00      0.90      0.95       125
           1       0.85      1.00      0.92        75

    accuracy                           0.94       200
   macro avg       0.93      0.95      0.93       200
weighted avg       0.94      0.94      0.94       200



### Extra Task - Implement a SPAM/HAM classifier

https://www.kaggle.com/t/b384e34013d54d238490103bc3c360ce

The classifier can not be changed!!! It must be the MultinimialNB with default parameters!

Your task is to find the **best feature representation**.

You can work with teams of two persons (recommended).

In [18]:
# Your code